In [7]:
# Imports

import json
from dataclasses import asdict, dataclass

import cadquery as cq

from teardrop import teardrop
from tools import show


In [8]:
# Dims


@dataclass
class PrinterAttchmntDims:
    __measured_base_to_lower_large_screw_hole_offset = 7.7
    __measured_base_to_upper_large_screw_hole_offset = 27.5
    __measured_screw_large_hole_radius = 8.9 / 2
    __measured_screw_small_hole_radius = 4.9 / 2
    __measured_screw_holes_edge_y_offset = 18.3

    tringle_side: float = 33.0
    tringle_height: float = 45.0
    screw_extr_depth: float = 27.0
    screw_tightening_wall_thickness: float = 0.8

    screw_extr_height: float = 11.0
    lower_to_upper_screw_extr_gap: float = 8.4
    screw_extn_to_triangle_edge_gap: float = 1.1
    screw_large_hole_radius: float = 9.3 / 2
    screw_small_hole_radius: float = 4.9 / 2

    screw_holes_center_y_offset: float = (
        __measured_screw_holes_edge_y_offset + __measured_screw_small_hole_radius
    )
    lower_screw_hole_center_z_offset: float = (
        __measured_base_to_lower_large_screw_hole_offset + __measured_screw_large_hole_radius
    )
    upper_screw_hole_center_z_offset: float = (
        __measured_base_to_upper_large_screw_hole_offset + __measured_screw_large_hole_radius
    )

    base_to_lower_screw_extr_offset: float = lower_screw_hole_center_z_offset - (
        screw_extr_height / 2
    )
    base_to_upper_screw_extr_offset: float = upper_screw_hole_center_z_offset - (
        screw_extr_height / 2
    )

    # Screw dims: core diameter 4.8  ; head diameter 9.4
    # The radius of the hole through which the whole screw pass through the adapter - must be
    # bigger than the head of the screw + some margin for ease of use
    screw_large_hole_radius: float = 10.4 / 2

    # The radius of the hole in the wall adjecent to the screw hole on the printer side. Must be
    # bigger than the screw core + some margin for ease of use
    screw_small_hole_radius: float = 5.3 / 2

    text_thickness: float = 0.8
    # As measured
    # lower_screw_extr_height = 11.5
    # upper_screw_extr_height = 14.0
    # lower_to_upper_screw_extr_gap = 8.4
    # screw_extn_to_triangle_edge_gap = 1.1
    # base_to_lower_screw_extr_offset = 7.5
    # base_to_upper_screw_extr_offset = (
    #     base_to_lower_screw_extr_offset + lower_screw_extr_height + lower_to_upper_screw_extr_gap
    # )
    # screw_large_hole_radius = 9.3 / 2
    # screw_small_hole_radius = 4.9 / 2
    # base_to_lower_large_screw_hole_offset = 8.4
    # base_to_upper_large_screw_hole_offset = 28.4

    fillet_radius = 0.6

    rod_holder_teardrop_radius: float = 3.0


@dataclass
class RodDims:
    core_height: float = 100.0
    teardrop_connector_height: float = 20.0
    teardrop_radius: float = PrinterAttchmntDims().rod_holder_teardrop_radius * 0.98
    core_radius = 6
    cam_adapter_edge_len: float = core_radius * 0.8
    total_height = core_height + teardrop_connector_height


@dataclass
class CamAdapterDims:
    cilinder_radius: float = 5.94 / 2
    cube_offset: float = 1.2
    cube_height: float = 4.4
    cillinder_height: float = 5.3

    rod_connector_base_side: float = RodDims().cam_adapter_edge_len * 0.93
    rod_connector_mid_side: float = RodDims().cam_adapter_edge_len * 0.98
    rod_connector_height: float = RodDims().cam_adapter_edge_len * 0.84

    mid_section_top_side: float = 13.0
    mid_section_height: float = 15.0

    # camera should be looking down
    camera_z_axis_angle: float = -12


print("d:")
print("PrinterAttchmntDims: ")
print(json.dumps(asdict(PrinterAttchmntDims()), indent=2))

d:
PrinterAttchmntDims: 
{
  "tringle_side": 33.0,
  "tringle_height": 45.0,
  "screw_extr_depth": 27.0,
  "screw_tightening_wall_thickness": 0.8,
  "screw_extr_height": 11.0,
  "lower_to_upper_screw_extr_gap": 8.4,
  "screw_extn_to_triangle_edge_gap": 1.1,
  "screw_large_hole_radius": 5.2,
  "screw_small_hole_radius": 2.65,
  "screw_holes_center_y_offset": 20.75,
  "lower_screw_hole_center_z_offset": 12.15,
  "upper_screw_hole_center_z_offset": 31.95,
  "base_to_lower_screw_extr_offset": 6.65,
  "base_to_upper_screw_extr_offset": 26.45,
  "text_thickness": 0.8,
  "rod_holder_teardrop_radius": 3.0
}


In [9]:
def make_screw_tunnel_extrusion():
    """Creates the cuboid that holds the screw tunnel.
    The thing that you insert into the gaps in the printer.
    """
    d = PrinterAttchmntDims()
    return (
        cq.Workplane("XY")
        .moveTo(d.screw_extn_to_triangle_edge_gap, 0)
        .lineTo(d.tringle_side, 0)
        .lineTo(d.tringle_side, d.screw_extr_depth)
        .lineTo(d.screw_extn_to_triangle_edge_gap, d.screw_extr_depth)
        .lineTo(d.screw_extn_to_triangle_edge_gap, 0)
        .close()
        .extrude(d.screw_extr_height)
        .fillet(d.fillet_radius)
    )


def make_screw_tunnel():
    d = PrinterAttchmntDims()
    large_hole = (
        teardrop(cq.Workplane("YZ"), d.screw_large_hole_radius, rotate=270)
        .extrude(d.tringle_side * 1.5)
        .translate((d.screw_tightening_wall_thickness + d.screw_extn_to_triangle_edge_gap, 0, 0))
    )

    small_hole = cq.Workplane("YZ").circle(d.screw_small_hole_radius).extrude(d.tringle_side * 1.5)
    all = large_hole + small_hole
    return all


def make_rod_holder() -> cq.Workplane:
    d = PrinterAttchmntDims()
    body = cq.Workplane("XY").rect(17, 14, centered=False).extrude(3)
    body = body.fillet(d.fillet_radius)
    teardrop_hole = (
        teardrop(cq.Workplane("XY"), radius=d.rod_holder_teardrop_radius)
        .extrude(3)
        .translate((9, 7, 0))
    )
    all = body - teardrop_hole

    return all


def make_printer_attachment():
    d = PrinterAttchmntDims()
    main_triangle = (
        cq.Workplane("XY")
        .moveTo(0, 0)
        .lineTo(d.tringle_side, 0)
        .lineTo(d.tringle_side, d.tringle_side)
        .lineTo(0, 0)
        .close()
        .extrude(d.tringle_height)
        .fillet(d.fillet_radius)
    )

    lower_screw_extr = make_screw_tunnel_extrusion().translate(
        (0, 0, d.base_to_lower_screw_extr_offset)
    )

    upper_screw_extr = make_screw_tunnel_extrusion().translate(
        (0, 0, d.base_to_upper_screw_extr_offset)
    )

    lower_screw_hole = make_screw_tunnel().translate(
        (0, d.screw_holes_center_y_offset, d.lower_screw_hole_center_z_offset)
    )
    upper_screw_hole = make_screw_tunnel().translate(
        (0, d.screw_holes_center_y_offset, d.upper_screw_hole_center_z_offset)
    )

    upper_screw_extr = upper_screw_extr
    lower_screw_extr = lower_screw_extr

    cam_text = (
        cq.Workplane("XZ")
        .text("cam", fontsize=10, distance=0)
        .extrude(d.text_thickness)
        .translate((20, d.text_thickness, 30))
    )

    rod_base_offset = 15.0
    rod_holders_offset = 8.0
    rod_holders_count = 3
    rod_holders = cq.Workplane()
    for i in range(rod_holders_count):
        rod_holders += make_rod_holder().translate(
            (d.tringle_side, 0, rod_base_offset + i * rod_holders_offset)
        )

    all = (
        main_triangle
        + lower_screw_extr
        + upper_screw_extr
        + rod_holders
        - cam_text
        - upper_screw_hole
        - lower_screw_hole
    )
    all = all.rotate((0, 0, 0), (1, 0, 0), 90)
    return all


def make_sampler():
    attachment = make_printer_attachment()
    min_x = 00
    max_x = 10
    min_y = 0
    max_y = 50
    cut_out = (
        cq.Workplane("XY")
        .moveTo(min_x, min_y)
        .lineTo(max_x, min_y)
        .lineTo(max_x, max_y)
        .lineTo(min_x, max_y)
        .lineTo(min_x, min_y)
        .close()
        .extrude(50)
    )
    sampler = attachment.intersect(cut_out)
    return sampler


sampler = make_sampler()
sampler.export("sampler.stl")
attchmnt = make_printer_attachment()
attchmnt.export("printer_attachment.stl")
show(attchmnt)


In [10]:
def make_rod():
    d = RodDims()
    tear_drop_connector = teardrop(cq.Workplane("XY"), radius=d.teardrop_radius).extrude(
        d.teardrop_connector_height
    )
    core = (
        cq.Workplane("XY")
        .circle(radius=d.core_radius)
        .extrude(d.core_height)
        .translate((0, 0, d.teardrop_connector_height))
    )

    gap_for_cam_adapter = (
        cq.Workplane("XY")
        .rect(d.cam_adapter_edge_len, d.cam_adapter_edge_len)
        .extrude(d.cam_adapter_edge_len)
        .translate((0, 0, d.teardrop_connector_height + d.core_height - d.cam_adapter_edge_len))
        .rotate((0, 0, 0), (0, 0, 1), 45)
    )
    all = tear_drop_connector + core - gap_for_cam_adapter

    all = all.rotate((-1, 0, d.total_height / 2), (1, 0, d.total_height / 2), 90)
    return all


rod = make_rod()
rod.export("rod.stl")
show(rod)


In [11]:
def make_camera_adapter():
    d = CamAdapterDims()
    cube = (
        cq.Workplane("XY")
        .transformed(rotate=(0, d.camera_z_axis_angle, 0))
        .rect(d.cilinder_radius * 2, d.cilinder_radius + d.cube_offset)
        .extrude(d.cube_height)
        .translate((0, d.cilinder_radius - d.cube_offset, 0))
    )
    cillinder = (
        cq.Workplane("XY")
        .transformed(rotate=(0, d.camera_z_axis_angle, 0))
        .circle(d.cilinder_radius)
        .extrude(d.cillinder_height)
    )

    cam_section = (cube + cillinder).translate(
        (0, 0, d.rod_connector_height + d.mid_section_height)
    )

    mid_section = (
        cq.Workplane("XY")
        .rect(d.rod_connector_mid_side, d.rod_connector_mid_side)  # base
        .workplane(offset=d.mid_section_height)
        .transformed(rotate=(0, d.camera_z_axis_angle, 0))
        .rect(d.mid_section_top_side, d.mid_section_top_side)  # top
        .loft()
        .translate((0, 0, d.rod_connector_height))
        .edges("not #Z")
        .fillet(0.6)
    )

    rod_section = (
        cq.Workplane("XY")
        .rect(d.rod_connector_base_side, d.rod_connector_base_side)
        .workplane(offset=d.rod_connector_height)
        .rect(d.rod_connector_mid_side, d.rod_connector_mid_side)
        .loft()
        .edges("not #Z")
        .fillet(0.6)
    )
    return rod_section + cam_section + mid_section


cam_adapter = make_camera_adapter()
cam_adapter.export("cam_adapter.stl")


show(cam_adapter)


In [12]:
def create_assembly():
    assembly = cq.Assembly()
    assembly.add(
        make_printer_attachment(),
        color=cq.Color("gray"),
        loc=cq.Location((0, 0, 0), (1, 0, 1), 180),
    )
    assembly.add(
        make_rod(),
        color=cq.Color("yellow"),
        loc=cq.Location((-53, 75, 42), (1, 0, 1), 180),
    )
    adapter = make_camera_adapter()
    adapter = adapter.rotate((-1, 0, 0), (1, 0, 0), 270)
    adapter = adapter.rotate((0, -1, 0), (0, 1, 0), 180 + 45)
    assembly.add(
        adapter,
        color=cq.Color("blue"),
        loc=cq.Location(
            (7, 135, 42),
        ),
    )

    return assembly


display(create_assembly())